In [1]:
!pip install transformers sentencepiece

     |████████████████████████████████| 9.1 MB 26.1 MB/s eta 0:00:01
     |████████████████████████████████| 1.3 MB 94.2 MB/s eta 0:00:01
     |████████████████████████████████| 19.3 MB 97.7 MB/s eta 0:00:01
     |████████████████████████████████| 1.2 MB 87.6 MB/s eta 0:00:01
     |████████████████████████████████| 3.6 MB 111.0 MB/s eta 0:00:01
     |████████████████████████████████| 774 kB 96.6 MB/s eta 0:00:01
     |████████████████████████████████| 402 kB 118.3 MB/s eta 0:00:01
     |████████████████████████████████| 176 kB 127.1 MB/s eta 0:00:01


In [1]:
from transformers import AutoModel

xlm_base = AutoModel.from_pretrained("xlm-roberta-base")

config.json:   0%|          | 0.00/615 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.12G [00:00<?, ?B/s]

In [2]:
xlm_large = AutoModel.from_pretrained("xlm-roberta-large")

config.json:   0%|          | 0.00/616 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.24G [00:00<?, ?B/s]

In [3]:
xlm_base

XLMRobertaModel(
  (embeddings): XLMRobertaEmbeddings(
    (word_embeddings): Embedding(250002, 768, padding_idx=1)
    (position_embeddings): Embedding(514, 768, padding_idx=1)
    (token_type_embeddings): Embedding(1, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): XLMRobertaEncoder(
    (layer): ModuleList(
      (0-11): 12 x XLMRobertaLayer(
        (attention): XLMRobertaAttention(
          (self): XLMRobertaSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): XLMRobertaSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=Tru

In [6]:
old_embeddings = xlm_base.embeddings.position_embeddings.weight.data
old_embeddings

tensor([[ 0.0578, -0.0071, -0.0068,  ...,  0.0061, -0.0260, -0.0291],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [-0.1564, -0.0728, -0.2477,  ..., -0.0778, -0.3088, -0.0090],
        ...,
        [ 0.0118,  0.0458, -0.0054,  ..., -0.0865,  0.0374,  0.0040],
        [ 0.0525, -0.0270, -0.0141,  ..., -0.0552,  0.0349,  0.0274],
        [-0.0479, -0.0293,  0.1079,  ..., -0.0825,  0.2908,  0.0861]])

In [7]:
old_embeddings.shape

torch.Size([514, 768])

In [8]:
import torch

new_embeddings = torch.zeros((2050, 768))

In [10]:
new_embeddings[:514, :] = old_embeddings.clone()

In [19]:
num_pos = 514

for i in range(3):
    start_idx = num_pos+512*i
    end_idx = start_idx + 512
    new_embeddings[start_idx:end_idx, :] = old_embeddings[2:, :].clone()
    print(start_idx, end_idx)

514 1026
1026 1538
1538 2050


In [30]:

xlm_base = AutoModel.from_pretrained("xlm-roberta-base", max_position_embeddings=2050, ignore_mismatched_sizes=True)

xlm_base.embeddings.position_embeddings.weight.data = new_embeddings

Some weights of XLMRobertaModel were not initialized from the model checkpoint at xlm-roberta-base and are newly initialized because the shapes did not match:
- roberta.embeddings.position_embeddings.weight: found shape torch.Size([514, 768]) in the checkpoint and torch.Size([2050, 768]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [31]:
with torch.no_grad():
    xlm_base(input_ids=seq_2048)

In [33]:
print(xlm_base.embeddings.position_embeddings.weight.data.shape)
xlm_base.embeddings.position_embeddings.weight.data

torch.Size([2050, 768])


tensor([[ 0.0578, -0.0071, -0.0068,  ...,  0.0061, -0.0260, -0.0291],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [-0.1564, -0.0728, -0.2477,  ..., -0.0778, -0.3088, -0.0090],
        ...,
        [ 0.0118,  0.0458, -0.0054,  ..., -0.0865,  0.0374,  0.0040],
        [ 0.0525, -0.0270, -0.0141,  ..., -0.0552,  0.0349,  0.0274],
        [-0.0479, -0.0293,  0.1079,  ..., -0.0825,  0.2908,  0.0861]])

In [34]:
old_embeddings = xlm_large.embeddings.position_embeddings.weight.data

new_embeddings = torch.zeros((2050, old_embeddings.shape[1]))

new_embeddings[:514, :] = old_embeddings.clone()

num_pos = 514

for i in range(3):
    start_idx = num_pos+512*i
    end_idx = start_idx + 512
    new_embeddings[start_idx:end_idx, :] = old_embeddings[2:, :].clone()
    print(start_idx, end_idx)

514 1026
1026 1538
1538 2050


In [35]:
xlm_large = AutoModel.from_pretrained("xlm-roberta-large", max_position_embeddings=2050, ignore_mismatched_sizes=True)

xlm_large.embeddings.position_embeddings.weight.data = new_embeddings

Some weights of XLMRobertaModel were not initialized from the model checkpoint at xlm-roberta-large and are newly initialized because the shapes did not match:
- roberta.embeddings.position_embeddings.weight: found shape torch.Size([514, 1024]) in the checkpoint and torch.Size([2050, 1024]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [37]:
!huggingface-cli login

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /home/user/.cache/huggingface/token
Login successful


In [38]:
xlm_large.push_to_hub("nbroad/xlm-roberta-large-2048")

model.safetensors:   0%|          | 0.00/2.25G [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/nbroad/xlm-roberta-large-2048/commit/8270d498aad31c695866c0fbcf5c7eb932b69590', commit_message='Upload model', commit_description='', oid='8270d498aad31c695866c0fbcf5c7eb932b69590', pr_url=None, pr_revision=None, pr_num=None)

In [39]:
xlm_base.push_to_hub("nbroad/xlm-roberta-base-2048")

model.safetensors:   0%|          | 0.00/1.12G [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/nbroad/xlm-roberta-base-2048/commit/4daea3ba9080f535f1fc819cbc76453248252f6b', commit_message='Upload model', commit_description='', oid='4daea3ba9080f535f1fc819cbc76453248252f6b', pr_url=None, pr_revision=None, pr_num=None)

In [40]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("xlm-roberta-base")

In [42]:
tokenizer.model_max_length = 2048

In [44]:
tokenizer.push_to_hub("nbroad/xlm-roberta-base-2048")

README.md:   0%|          | 0.00/5.17k [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/nbroad/xlm-roberta-base-2048/commit/82129a4b55ea013dd3fa2816c24696814b08a6b4', commit_message='Upload tokenizer', commit_description='', oid='82129a4b55ea013dd3fa2816c24696814b08a6b4', pr_url=None, pr_revision=None, pr_num=None)

In [45]:
tokenizer = AutoTokenizer.from_pretrained("xlm-roberta-large").push_to_hub("nbroad/xlm-roberta-large-2048")
tokenizer.model_max_length = 2048
tokenizer.push_to_hub("nbroad/xlm-roberta-large-2048")

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.10M [00:00<?, ?B/s]

README.md:   0%|          | 0.00/5.17k [00:00<?, ?B/s]

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

AttributeError: 'CommitInfo' object has no attribute 'push_to_hub'